# 23. LLM test

# PICKLE and Load Variables

In [1]:
import pickle
def pkl_vars(varname, filename):
    with open(filename, 'wb') as file:
        pickle.dump(varname, file)
        
def reload_vars(filename):
    this_var = None
    with open(filename, 'rb') as file:
        this_var = pickle.load(file)      
    return this_var

In [59]:
pkl_vars(answers, 'data/vars/math_mistralv2_answers_20250209.pkl')

In [103]:
pkl_vars(answers, 'data/vars/math_mistralv2_answers_20250210.pkl')

In [120]:
pkl_vars(answers, 'data/vars/math_mistralv2_answers_20250210_1251.pkl')

In [220]:
pkl_vars(results, 'data/vars/math_mistralv2_results_20250210_lax.pkl')

In [223]:
pkl_vars(results, 'data/vars/math_mistralv2_results_20250210_strict.pkl')

In [48]:
pkl_vars(results, 'data/vars/math_mistralv2_test_raw_answers_20250211.pkl')

In [2]:
term_dict = reload_vars('data/vars/def_disamb_kb.pkl')
term_dict

{'Boundary': ['Definition:Boundary (Geometry)',
  'Definition:Boundary (Topology)',
  'Definition:Boundary (Graph Theory)'],
 'Right': ['Definition:Right (Direction)',
  'Definition:Right Angle',
  'Definition:Right Hand Side',
  'Definition:Right-Total Relation',
  'Definition:Right Quasi-Reflexive Relation',
  'Definition:Euclidean Relation/Right-Euclidean',
  'Definition:Right Normal Element of Relation',
  'Definition:Right Cancellable Mapping',
  'Definition:Right Inverse Mapping',
  'Definition:Interval/Ordered Set/Right Half-Open',
  'Definition:Orientation of Coordinate Axes/Cartesian Plane/Right-Handed',
  'Definition:Orientation of Coordinate Axes/Cartesian 3-Space/Right-Handed',
  'Definition:Limit of Real Function/Right',
  'Definition:Difference Quotient/Right',
  'Definition:Continuous Real Function/Right-Continuous',
  'Definition:Right-Hand Derivative/Real Function',
  'Definition:Real Interval/Half-Open/Right',
  'Definition:Real Interval/Unbounded Closed',
  'Definiti

In [12]:
!pip install huggingface_hub

In [14]:
from huggingface_hub import notebook_login
notebook_login()

https://huggingface.co/mistralai/Mistral-7B-Instruct-v0.3

# Mistral v2

In [10]:
pip install torch --pre --extra-index-url https://download.pytorch.org/whl/nightly/cu116

Looking in indexes: https://pypi.org/simple, https://download.pytorch.org/whl/nightly/cu116
Note: you may need to restart the kernel to use updated packages.


In [9]:
pip install torch==1.13.1+cu116 -f https://download.pytorch.org/whl/torch_stable.html

Looking in links: https://download.pytorch.org/whl/torch_stable.html
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 GB 1.4 MB/s eta 0:00:000:00:0100:01
  Attempting uninstall: torch
    Found existing installation: torch 2.3.0
    Uninstalling torch-2.3.0:
      Successfully uninstalled torch-2.3.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
xformers 0.0.26.post1 requires torch==2.3.0, but you have torch 1.13.1+cu116 which is incompatible.
transformer-smaller-training-vocab 0.3.3 requires sentencepiece<0.2.0,>=0.1.97, but you have sentencepiece 0.2.0 which is incompatible.
torch-max-mem 0.1.3 requires torch>=2.0, but you have torch 1.13.1+cu116 which is incompatible.
pykeen 1.10.3.dev0 requires torch>=2.0, but you have torch 1.13.1+cu116 which is incompatible.
Note: you may need to restart the kernel to use updated packages.


In [3]:
import torch
torch.zeros(1).cuda()
torch.cuda.is_available()
device = "cuda:0" if torch.cuda.is_available() else "cpu"
device

'cuda:0'

In [4]:
from transformers import AutoModelForCausalLM, AutoTokenizer


model = AutoModelForCausalLM.from_pretrained("mistralai/Mistral-7B-Instruct-v0.2")
tokenizer = AutoTokenizer.from_pretrained("mistralai/Mistral-7B-Instruct-v0.2")

if tokenizer.pad_token is None:
        tokenizer.pad_token = tokenizer.eos_token

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

In [5]:
setting = "Your task is to disambiguate mathematical definitions.\n"

In [6]:
no_answer = "Reply with \"I don\'t know\" when uncertain. \n"

In [7]:
no_explanation = "Only answer with the number corresponding to the correct choice in the provided list. \nDo not provide justifications.\n"

In [8]:
definition = "\n\nFor example, the endpoints of a line segment are its boundaries.\n\n\n=== Containment ===\nA geometric figure is said to be contained by its boundary or boundaries.\n\n "

In [9]:
term = "\'Boundary\'"

In [10]:
choices = ['1. Boundary (Geometry)',
  '2. Boundary (Topology)',
  '3. Boundary (Graph Theory)']

In [11]:
test_inst = setting + no_answer + no_explanation + \
            "Identify the correct definition title from this list: \n" + "\n".join(choices) + \
            "\n\n Given the term \"" + term + \
            "\" and the following definition as context: \n" + definition
print(test_inst)

Your task is to disambiguate mathematical definitions.
Reply with "I don't know" when uncertain. 
Only answer with the number corresponding to the correct choice in the provided list. 
Do not provide justifications.
Identify the correct definition title from this list: 
1. Boundary (Geometry)
2. Boundary (Topology)
3. Boundary (Graph Theory)

 Given the term "'Boundary'" and the following definition as context: 


For example, the endpoints of a line segment are its boundaries.


=== Containment ===
A geometric figure is said to be contained by its boundary or boundaries.

 


In [12]:
messages = [{"role": "user", "content": test_inst}]

encodeds = tokenizer.apply_chat_template(messages, return_tensors="pt")

model_inputs = encodeds.to(device)
model.to(device)

generated_ids = model.generate(model_inputs, max_new_tokens=1000, do_sample=True, pad_token_id=tokenizer.eos_token_id)
decoded = tokenizer.batch_decode(generated_ids)
print(decoded)

['<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. \nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide justifications.\nIdentify the correct definition title from this list: \n1. Boundary (Geometry)\n2. Boundary (Topology)\n3. Boundary (Graph Theory)\n\n Given the term "\'Boundary\'" and the following definition as context: \n\n\nFor example, the endpoints of a line segment are its boundaries.\n\n\n=== Containment ===\nA geometric figure is said to be contained by its boundary or boundaries.\n\n  [/INST] 1. Boundary (Geometry)</s>']


In [13]:
def get_choices(term):
    choices = list()
    for idx, choice in enumerate(term_dict[term]):
        text = f'{idx+1}. {choice.split(":")[-1]}'        
        choices.append(text)
    return choices    
    

get_choices("Boundary")

['1. Boundary (Geometry)',
 '2. Boundary (Topology)',
 '3. Boundary (Graph Theory)']

In [14]:
ANSWERS = list()
TOTAL_TIME = 0

In [15]:
df_test = reload_vars('data/vars/flattened_test_disam_list.pkl')
len(df_test)

433

In [16]:
from rich.progress import track, Progress
from rich import print
import datetime, time

def run_test(data, offset):
    global ANSWERS
    global TOTAL_TIME
    messages = list()

    print(datetime.datetime.now())

    with Progress() as progress:

        task1 = progress.add_task("[blue] Prompt sample [%s]" % (len(data)-offset), total=len(data)-offset)

        for idx, elem in enumerate(data[offset:]):
            progress.update(task1, advance=1)

            choices = get_choices(elem['term'])
            inst = setting + \
                no_answer + \
                no_explanation + \
                "Identify the correct definition title from this list: \n" + "\n".join(choices) +\
                "\nGiven the term " + elem['term'] + \
                "and the following definition as context: \n" + elem['definition']

            #messages.append([{"role": "user", "content": inst}])
            messages = [{"role": "user", "content": inst}]

            #print(f'start [{idx}]: {datetime.datetime.now()}')
            start = time.time()
            encodeds = tokenizer.apply_chat_template(messages, return_tensors="pt")

            model_inputs = encodeds.to(device)
            model.to(device)
            generated_ids = model.generate(model_inputs, max_new_tokens=1000, do_sample=True, pad_token_id=tokenizer.eos_token_id)
            decoded = tokenizer.batch_decode(generated_ids)

            end = time.time()
            elapsed_time = end - start
            TOTAL_TIME += elapsed_time
            print(f'[{idx + offset}] {elapsed_time}')

            ANSWERS.append((idx, elem['definition'].split(':')[-1], decoded[0]))        

In [17]:
run_test(df_test, 0)

2025-02-11 14:32:55.651677

Output()

[0] 0.5445981025695801

[1] 0.9369173049926758

[2] 0.5941345691680908

...

[92] 0.635977029800415

[93] 2.6392452716827393

[94] 1.4674055576324463

[95] 0.6382973194122314

OutOfMemoryError: CUDA out of memory. Tried to allocate 902.00 MiB (GPU 0; 31.75 GiB total capacity; 29.17 GiB already allocated; 739.69 MiB free; 30.06 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

In [18]:
print(TOTAL_TIME)
print(len(ANSWERS))

249.16008067131042

96

In [21]:
run_test(df_test, offset = 97)

2025-02-11 14:51:49.281418

Output()

[97] 1.6638500690460205

[98] 0.5278043746948242

[99] 1.343970537185669

...

[408] 0.48844289779663086

[409] 0.7477281093597412

[410] 15.419939517974854

[411] 0.6280457973480225

OutOfMemoryError: CUDA out of memory. Tried to allocate 2.11 GiB (GPU 0; 31.75 GiB total capacity; 28.97 GiB already allocated; 1.53 GiB free; 29.25 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

In [22]:
print(TOTAL_TIME)
print(len(ANSWERS))

940.4040477275848

411

In [24]:
run_test(df_test, offset = 413)

2025-02-11 15:05:50.371298

Output()

[413] 0.9686219692230225

[414] 0.5846145153045654

[415] 0.9463071823120117

...

[428] 0.7121427059173584

[429] 0.8977112770080566

[430] 0.7471542358398438

[431] 0.8304927349090576

[432] 2.758233070373535

In [26]:
print(TOTAL_TIME)
print(len(ANSWERS))

974.1415002346039

431

# Problematic items

In [27]:
df_test[96]

{'title': 'Definition:Matrix Product',
 'term': 'Product',
 'definition': "=== Matrix Product (Conventional) ===\nLet ( R, +, ∘) be a ring.\n\nLet 𝐀 = [ a ]_m n be an m × n matrix over R.\n\nLet 𝐁 = [ b ]_n p be an n × p matrix over R.\n\nThen the matrix product of 𝐀 and 𝐁 is written 𝐀𝐁 and is defined as follows.\n\nLet 𝐀𝐁 = 𝐂 = [ c ]_m p.\n\n\nThen:\n:∀ i ∈[ 1  . . ]m, j ∈[ 1  . . ]p: c_i j = ∑_k  = 1^n a_i k∘ b_k j\n\n\nThus [ c ]_m p is the m × p matrix where each entry c_i j is built by forming the (ring) product of each entry in the i'th row of 𝐀 with the corresponding entry in the j'th column of 𝐁 and adding up all those products.\n\n\nThis operation is called matrix multiplication, and 𝐂 is the matrix product of 𝐀 with 𝐁.\n\n\nIt follows that matrix multiplication is defined whenever the first matrix has the same number of columns as the second matrix has rows.\n\n\n=== Pre-Multiplication ===\nLet ( R, +, ∘) be a ring.\n\nLet 𝐀 = [ a ]_m n be an m × n matrix over R.\n\nLet 𝐁 = [

In [28]:
df_test[412]

{'title': 'Definition:Leibniz Harmonic Triangle',
 'term': 'Harmonic',
 'definition': "The Leibniz Harmonic Triangle is a triangular array where:\n:the zeroth element in the nth row, counting from 0, is 1 n + 1\n:subsequent elements in the nth row are the zeroth element divided by the corresponding element of Pascal's triangle:\n\n\n:[    n    0    1    2    3    4    5;    0  1/1;    1  1/2  1/2;    2  1/3  1/6  1/3;    3  1/4 1/12 1/12  1/4;    4  1/5 1/20 1/30 1/20  1/5;    5  1/6 1/30 1/60 1/60 1/30  1/6;      ]\n\n\n=== Row ===\nConsider the Leibniz harmonic triangle:\nThe Leibniz Harmonic Triangle is a triangular array where:\n:the zeroth element in the nth row, counting from 0, is 1 n + 1\n:subsequent elements in the nth row are the zeroth element divided by the corresponding element of Pascal's triangle:\n\n\n:[    n    0    1    2    3    4    5;    0  1/1;    1  1/2  1/2;    2  1/3  1/6  1/3;    3  1/4 1/12 1/12  1/4;    4  1/5 1/20 1/30 1/20  1/5;    5  1/6 1/30 1/60 1/60 1/

# Analysis

In [29]:
len(ANSWERS)

431

In [122]:
answers[0]

(' \n\nFor example, the endpoints of a line segment are its boundaries.\n\n\n=== Containment ===\nA geometric figure is said to be contained by its boundary or boundaries.\n\n ',
 '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. \nOnly answer with the number corresponding to the correct choice. \nDo not provide justifications.\nGiven this mathematical definition: \n \n\nFor example, the endpoints of a line segment are its boundaries.\n\n\n=== Containment ===\nA geometric figure is said to be contained by its boundary or boundaries.\n\n \nThe term Boundary, corresponds to which terms in this list: \n1. Boundary (Geometry)\n2. Boundary (Topology)\n3. Boundary (Graph Theory) [/INST] 1. Boundary (Geometry)</s>')

In [30]:
import re

def clean_answers(raw_answers):
    cleaned_answers = list()

    for answer in raw_answers:
        print(answer)
        
        idx = answer[0]
        
        answer = " ".join(answer[1:])
        pos = answer.find("[/INST] ")

        answer_str = answer[pos+11:-4]
        matches = re.match('^([0-9]+)\.', answer[pos+8:])
        answer_num = -1
        if not matches is None:
            answer_num = matches.group(1)

        #print(answer_num, answer_str)

        cleaned_answers.append((idx, answer_str, answer_num))
        
    return cleaned_answers

In [31]:
test_cleaned_answers = clean_answers(ANSWERS)

(
    0,
    ' \n\nFor example, the endpoints of a line segment are its boundaries.\n\n\n=== Containment ===\nA geometric 
figure is said to be contained by its boundary or boundaries.\n\n ',
    '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. 
\nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide 
justifications.\nIdentify the correct definition title from this list: \n1. Boundary (Geometry)\n2. Boundary 
(Topology)\n3. Boundary (Graph Theory)\nGiven the term Boundaryand the following definition as context: \n \n\nFor 
example, the endpoints of a line segment are its boundaries.\n\n\n=== Containment ===\nA geometric figure is said 
to be contained by its boundary or boundaries.\n\n  [/INST] 1. Boundary (Geometry)</s>'
)

(
    1,
    'H^e denotes the exterior of H.',
    '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. 
\nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide 
justifications.\nIdentify the correct definition title from this list: \n1. Boundary (Geometry)\n2. Boundary 
(Topology)\n3. Boundary (Graph Theory)\nGiven the term Boundaryand the following definition as context: \nLet T = (
S, τ) be a topological space.\n\nLet H ⊆ S.\n\n\n=== Definition from Closure and Interior ===\nLet T = ( S, τ) be a
topological space.\n\nLet H ⊆ S.\n\n\nThe boundary of H consists of all the points in the closure of H which are 
not in the interior of H.\n\nThus, the boundary of H is defined as:\n:∂ H := H^- ∖ H^∘\nwhere H^- denotes the 
closure and H^∘ the interior of H.\n\n=== Definition from Neighborhood ===\nLet T = ( S, τ) be a topological 
space.\n\nLet H ⊆ S.\n\n\n \n\nx ∈ S is a boundary point of H  if and only if  every neighborhood N of x 
satisfies:\n:H ∩ N ∅\nand\n:H∩ N ∅\nwhere H is the complement of H in S.\n\nThe boundary of H consists of all the 
boundary point of H.\n\n=== Definition from Intersection of Closure with Closure of Complement ===\nLet T = ( S, τ)
be a topological space.\n\nLet H ⊆ S.\n\n\nThe boundary of H is the intersection of the closure of H with the 
closure of the complement of H in T:\n\n:∂ H = H^- ∩( H)^-\n\n=== Definition from Closure and Exterior ===\nLet T =
( S, τ) be a topological space.\n\nLet H ⊆ S.\n\n\nThe boundary of H consists of all the points in H which are not 
in either the interior or exterior of H.\n\nThus, the boundary of H is defined as:\n:∂ H := H ∖( H^∘∪ H^e 
)\nwhere:\n:H^∘ denotes the interior of H\n:H^e denotes the exterior of H. [/INST] 1. (Topology)</s>'
)

(
    2,
    ' { u, v }∈ E }',
    '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. 
\nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide 
justifications.\nIdentify the correct definition title from this list: \n1. Boundary (Geometry)\n2. Boundary 
(Topology)\n3. Boundary (Graph Theory)\nGiven the term Boundaryand the following definition as context: \n=== 
Simple Graph ===\nLet G = ( V, E ) be a simple graph.\n\nLet v ∈ V be a vertex of G.\n\n\nThen the boundary of v is
the set of all vertices of G which are adjacent to v:\n:B (   )v = { u ∈ V: { u, v }∈ E } [/INST] 3. Boundary 
(Graph Theory)</s>'
)

(
    3,
    '→',
    '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. 
\nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide 
justifications.\nIdentify the correct definition title from this list: \n1. Right (Direction)\n2. Right Angle\n3. 
Right Hand Side\n4. Right-Total Relation\n5. Right Quasi-Reflexive Relation\n6. Euclidean 
Relation/Right-Euclidean\n7. Right Normal Element of Relation\n8. Right Cancellable Mapping\n9. Right Inverse 
Mapping\n10. Interval/Ordered Set/Right Half-Open\n11. Orientation of Coordinate Axes/Cartesian 
Plane/Right-Handed\n12. Orientation of Coordinate Axes/Cartesian 3-Space/Right-Handed\n13. Limit of Real 
Function/Right\n14. Difference Quotient/Right\n15. Continuous Real Function/Right-Continuous\n16. Right-Hand 
Derivative/Real Function\n17. Real Interval/Half-Open/Right\n18. Real Interval/Unbounded Closed\n19. Real 
Interval/Unbounded Open\n20. Right Zero\n21. Identity (Abstract Algebra)/Right Identity\n22. Right Operation\n23. 
Cancellable Element/Right Cancellable\n24. Right Cancellable Operation\n25. Distributive Operation/Right\n26. 
Inverse (Abstract Algebra)/Right Inverse\n27. Quasigroup/Right Quasigroup\n28. Regular Representations/Right 
Regular Representation\n29. Operation/Binary Operation/Product/Right\n30. Right Naturally Totally Ordered 
Semigroup\n31. Coset/Right Coset\n32. Coset Space/Right Coset Space\n33. Transversal (Group Theory)/Right 
Transversal\n34. Group Action/Right Group Action\n35. Subset Product Action/Right\n36. Congruence Modulo 
Subgroup/Right Congruence\n37. Right Zero Divisor\n38. Linear Ring Action/Right\n39. Ideal of Ring/Right Ideal\n40.
Maximal Ideal of Ring/Right\n41. Right Module\n42. Right-Truncatable Prime\n43. Category of Right Modules\nGiven 
the term Rightand the following definition as context: \nThe direction right is that way:\n:→ [/INST] 1. Right 
(Direction)</s>'
)

(
    4,
    'A right angle is an angle that is equal to half of a straight angle.\n\n\n=== Measurement of Right Angle ===\n
',
    '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. 
\nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide 
justifications.\nIdentify the correct definition title from this list: \n1. Right (Direction)\n2. Right Angle\n3. 
Right Hand Side\n4. Right-Total Relation\n5. Right Quasi-Reflexive Relation\n6. Euclidean 
Relation/Right-Euclidean\n7. Right Normal Element of Relation\n8. Right Cancellable Mapping\n9. Right Inverse 
Mapping\n10. Interval/Ordered Set/Right Half-Open\n11. Orientation of Coordinate Axes/Cartesian 
Plane/Right-Handed\n12. Orientation of Coordinate Axes/Cartesian 3-Space/Right-Handed\n13. Limit of Real 
Function/Right\n14. Difference Quotient/Right\n15. Continuous Real Function/Right-Continuous\n16. Right-Hand 
Derivative/Real Function\n17. Real Interval/Half-Open/Right\n18. Real Interval/Unbounded Closed\n19. Real 
Interval/Unbounded Open\n20. Right Zero\n21. Identity (Abstract Algebra)/Right Identity\n22. Right Operation\n23. 
Cancellable Element/Right Cancellable\n24. Right Cancellable Operation\n25. Distributive Operation/Right\n26. 
Inverse (Abstract Algebra)/Right Inverse\n27. Quasigroup/Right Quasigroup\n28. Regular Representations/Right 
Regular Representation\n29. Operation/Binary Operation/Product/Right\n30. Right Naturally Totally Ordered 
Semigroup\n31. Coset/Right Coset\n32. Coset Space/Right Coset Space\n33. Transversal (Group Theory)/Right 
Transversal\n34. Group Action/Right Group Action\n35. Subset Product Action/Right\n36. Congruence Modulo 
Subgroup/Right Congruence\n37. Right Zero Divisor\n38. Linear Ring Action/Right\n39. Ideal of Ring/Right Ideal\n40.
Maximal Ideal of Ring/Right\n41. Right Module\n42. Right-Truncatable Prime\n43. Category of Right Modules\nGiven 
the term Rightand the following definition as context: \nA right angle is an angle that is equal to half of a 
straight angle.\n\n\n=== Measurement of Right Angle ===\n  [/INST] 2. Right Angle</s>'
)

...

(
    15,
    'APPB = -AQQB\n\n\nThen ( AB, PQ ) are said to be a harmonic range.',
    '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. 
\nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide 
justifications.\nIdentify the correct definition title from this list: \n1. Harmonic Mean\n2. Harmonic 
Numbers/General Definition\n3. Ore Number\n4. Leibniz Harmonic Triangle\n5. Harmonic Function\n6. Harmonic 
Analysis\n7. Harmonic Sequence\n8. Mercator\'s Constant\n9. Harmonic Series/General\n10. Harmonic (Analysis)\n11. 
Spherical Harmonic\n12. Surface Harmonic\n13. Tesseral Harmonic\n14. Sectoral Harmonic\n15. Zonal Harmonic\n16. 
Harmonic Potential Energy\n17. Harmonic Oscillator\n18. Simple Harmonic Motion\n19. Harmonic Ratio\n20. Harmonic 
Range\n21. Harmonic Conjugates\n22. Harmonic Pencil\nGiven the term Harmonicand the following definition as 
context: \nLet A and B be points on a straight line.\n\nLet P and Q lie on AB such that P is on the line segment AB
while Q is outside the line segment AB.\n\n\n:\n\n\nLet P and Q be positioned such that the cross-ratio { A, B; P, 
Q } forms a harmonic ratio:\n:APPB = -AQQB\n\n\nThen ( AB, PQ ) are said to be a harmonic range. [/INST] 20. 
Harmonic Range</s>'
)

(
    16,
    '\n\n\nThe rays OP and OQ are said to be harmonic conjugates with respect to OA and OB.',
    '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. 
\nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide 
justifications.\nIdentify the correct definition title from this list: \n1. Harmonic Mean\n2. Harmonic 
Numbers/General Definition\n3. Ore Number\n4. Leibniz Harmonic Triangle\n5. Harmonic Function\n6. Harmonic 
Analysis\n7. Harmonic Sequence\n8. Mercator\'s Constant\n9. Harmonic Series/General\n10. Harmonic (Analysis)\n11. 
Spherical Harmonic\n12. Surface Harmonic\n13. Tesseral Harmonic\n14. Sectoral Harmonic\n15. Zonal Harmonic\n16. 
Harmonic Potential Energy\n17. Harmonic Oscillator\n18. Simple Harmonic Motion\n19. Harmonic Ratio\n20. Harmonic 
Range\n21. Harmonic Conjugates\n22. Harmonic Pencil\nGiven the term Harmonicand the following definition as 
context: \n=== Harmonic Range ===\nLet AB and PQ be line segments on a straight line such that ( AB, PQ ) is a 
harmonic range.\n\nThen P and Q are said to be harmonic conjugates with respect to A and B.\n\n=== Harmonic Pencil 
===\nLet AB and PQ be line segments on a straight line such that ( AB, PQ ) is a harmonic range.\n\nLet O be a 
point which is not on the straight line AB.\n\nLet O (   )AB, PQ be the harmonic pencil formed from O and ( AB, PQ 
).\n\n\n:\n\n\nThe rays OP and OQ are said to be harmonic conjugates with respect to OA and OB. [/INST] 21. 
Harmonic Conjugates</s>'
)

(
    17,
    '\n\n\nThen the pencil O (   )AB, PQ formed by joining O to the four points A, B, P and Q is said to be a 
harmonic pencil.',
    '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. 
\nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide 
justifications.\nIdentify the correct definition title from this list: \n1. Harmonic Mean\n2. Harmonic 
Numbers/General Definition\n3. Ore Number\n4. Leibniz Harmonic Triangle\n5. Harmonic Function\n6. Harmonic 
Analysis\n7. Harmonic Sequence\n8. Mercator\'s Constant\n9. Harmonic Series/General\n10. Harmonic (Analysis)\n11. 
Spherical Harmonic\n12. Surface Harmonic\n13. Tesseral Harmonic\n14. Sectoral Harmonic\n15. Zonal Harmonic\n16. 
Harmonic Potential Energy\n17. Harmonic Oscillator\n18. Simple Harmonic Motion\n19. Harmonic Ratio\n20. Harmonic 
Range\n21. Harmonic Conjugates\n22. Harmonic Pencil\nGiven the term Harmonicand the following definition as 
context: \nLet A and B be points on a straight line.\n\nLet P and Q lie on AB such that ( AB, PQ ) is a harmonic 
range.\n\n\nLet O be a point which is not on the straight line AB.\n\n\n:\n\n\nThen the pencil O (   )AB, PQ formed
by joining O to the four points A, B, P and Q is said to be a harmonic pencil. [/INST] 22. Harmonic Pencil</s>'
)

(
    18,
    'Definitions/Infinite Products',
    '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. 
\nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide 
justifications.\nIdentify the correct definition title from this list: \n1. Divergent Product/Divergence to 
Zero\n2. Divergence Operator\nGiven the term Divergenceand the following definition as context: \nLet ( 𝕂, ‖ · ‖) 
be a valued field.\n\nLet ⟨ a_n ⟩ be a sequence of elements of 𝕂.\n\n\nIf either:\n\n:there exist infinitely many n
∈ℕ with a_n = 0\n\n:there exists n_0 ∈ℕ with a_n  0 for all n > n_0 and the sequence of partial products of ∏_n  = 
n_0 + 1^∞ a_n converges to 0\n\nthe product diverges to 0, and we assign the value:\n:∏_n  = 1^∞ a_n = 
0\n\n\nCategory:Definitions/Divergent Products\nCategory:Definitions/Infinite Products [/INST] 1. Divergent 
Product/Divergence to Zero</s>'
)

(
    19,
    '∫_S denotes the surface integral over S.',
    '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when uncertain. 
\nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide 
justifications.\nIdentify the correct definition title from this list: \n1. Divergent Product/Divergence to 
Zero\n2. Divergence Operator\nGiven the term Divergenceand the following definition as context: \n=== Physical 
Interpretation ===\nLet 𝐕 be a vector field acting over a region of space R.\n\nThe divergence of 𝐕 at a point P is
the total flux away from P per unit volume.\n\nIt is a scalar field.\n\n=== Geometrical Representation ===\nLet R 
be a region of space embedded in a Cartesian coordinate frame.\n\nLet 𝐕 be a vector field acting over R.\n\n\nThe 
divergence of 𝐕 at a point A in R is defined as:\n\n \n \n \n \n\nwhere:\n:∇ denotes the Del operator\n:· denotes 
the dot product\n:V_x, V_y and V_z denote the magnitudes of the components of 𝐕 at A in the directions of the 
coordinate axes x, y and z respectively.\n\n=== Real Cartesian Space ===\nLet ℝ^n (   )x_1, x_2, …, x_n denote the 
real Cartesian space of n dimensions.\n\nLet ( 𝐞_1, 𝐞_2, …, 𝐞_n ) be the standard ordered basis on ℝ^n.\n\nLet 𝐟 = 
( f_1 (   )𝐱, f_2 (   )𝐱, …, f_n (   )𝐱): ℝ^n →ℝ^n be a vector-valued function on ℝ^n.\n\n\nLet the partial 
derivative of 𝐟 with respect to x_k exist for all f_k.\n\n\nThe divergence of 𝐟 is defined as:\n\n \n \n \n \n 
\n\n\n=== Cartesian 3-Space ===\n\nIn 3 dimensions with the standard ordered basis ( 𝐢, 𝐣, 𝐤), this is usually 
rendered:\n\nLet R be a region of Cartesian 3-space ℝ^3.\n\nLet 𝐕(   )x, y, z be a vector field acting over 
R.\n\n\nThe divergence of 𝐕 is defined as:\n\n \n \n \n \n\n=== Riemannian Manifold ===\nLet ( M, g ) be a 
Riemannian manifold equiped with a metric g.\n\nLet 𝐗 : 𝒞^∞(   )M →𝒞^∞(   )M be a smooth vector field.\n\n\nThe 
divergence of 𝐗 is defined as:\n\n \n \n \n \n\nwhere:\n:⋆_g is the Hodge star operator of ( M, g )\n:d_d R is de 
Rham differential.\n\n=== Integral Form ===\nLet R be a region of space embedded in a Cartesian coordinate 
frame.\n\nLet 𝐕 be a vector field acting over R.\n\n\nThe divergence of 𝐕 at a point A in R is defined as:\n\n:div𝐕
:= lim_δτ→ 0∫_S 𝐕·d Sδτ\n\nwhere:\n:S is the surface of a volume element δτ containing A\n:· denotes the dot 
product\n:∫_S denotes the surface integral over S. [/INST] 1. Divergent Product/Divergence to Zero. (However, the 
context suggests the second option is more likely, as it matches the definition of divergence in the given physical
and geometrical contexts.)</s>'
)

In [32]:
print(test_cleaned_answers[33])

(
    33,
    ' Coset\n32. Coset Space\n33. Transversal\n34. Group Action\n35. Subset Product Action\n36. Congruence Modulo 
Subgroup\n\nThe given definition is discussing right cosets, which are a concept related to group actions, 
subgroups, and cosets. The term "Right" in this context indicates that we\'re working with right cosets, as opposed
to left cosets. The definition given specifies the calculation of a right coset using the subgroup H and an element
y from the group S. Therefore, the correct answers are the terms related to these concepts.',
    '31'
)

In [38]:
df_dict = reload_vars('data/vars/def_disamb_kb.pkl')
len(df_dict)

343

In [39]:
def analyze(df_train, cleaned_answers, raw_answer):
    results = list()
    correct_count = 0

    for answer_idx, elem in enumerate(cleaned_answers):
        idx, answer, pred_count = elem
        gt = df_train[idx]['title'].split('Definition:')[-1]

        is_correct = False
        #if gt.lower().strip() in answer[1].lower().strip(): #lax
        if answer.lower().strip() in gt.lower().strip(): #strict
            is_correct = True
            correct_count += 1
        else:
            prelim_answer = answer.split('\n')[0]
            if prelim_answer.lower().strip() in gt.lower().strip():
                correct_count += 1
                is_correct = True
            else:
                find_pos = prelim_answer.find('(')
                keyword = prelim_answer[:find_pos+1].strip()
                keyword = keyword.replace('\.$', '')
                dict_values = df_dict.get(keyword, [])

                if dict_values:
                    find_pos = prelim_answer.find(')')
                    title = prelim_answer[:find_pos+1]
                    try:
                        idx = dict_values.index(title)

                        if idx == answer[0]:
                            is_correct = True
                            correct_count += 1
                    except:
                        pass

        results.append({
            'idx': idx,
            'gt': gt,
            'pred_num': pred_count,
            'pred': answer,
            'is_correct': is_correct,
            'orig_answer': raw_answer[answer_idx]
        })
    print(f'Total correct: {correct_count}')
    return results

In [40]:
results = analyze(df_test, test_cleaned_answers, ANSWERS)

Total correct: 47

# ERROR Analysis

In [44]:
incorrect_list = list()

correct_count = 0
for result in results:
    if not result['is_correct']:
        incorrect_list.append(result)
    else:
        correct_count += 1

In [45]:
print(correct_count)

47

In [47]:
print(incorrect_list)

[
    {
        'idx': 5,
        'gt': 'Right Hand Side',
        'pred_num': '13',
        'pred': ' Limit of Real Function/Right\n14. Difference Quotient/Right\n15. Continuous Real 
Function/Right-Continuous\n16. Real Interval/Half-Open/Right\n17. Real Interval/Unbounded Closed\n18. Real 
Interval/Unbounded Open\n19. Right Zero\n20. Identity (Abstract Algebra)/Right Identity\n21. Right Operation\n22. 
Cancellable Element/Right Cancellable\n23. Right Cancellable Operation\n24. Distributive Operation/Right\n25. 
Inverse (Abstract Algebra)/Right Inverse\n26. Quasigroup/Right Quasigroup\n27. Regular Representations/Right 
Regular Representation\n28. Operation/Binary Operation/Product/Right\n31. Coset/Right Coset\n32. Coset Space/Right 
Coset Space\n34. Group Action/Right\n35. Subset Product Action/Right\n36. Congruence Modulo Subgroup/Right 
Congruence\n39. Right Module\n41. Right Module\n43. Category of Right Modules\n\nThe term on the right hand side of
an equation is a Right Module, a Right Coset, or a Right Hand Side. Based on the context provided, it is the Right 
Hand Side. Therefore, the answer is 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 26, 27, 28, 31, 32, 34, 35, 36,
39, or 41. The correct answer is 16, since the context specifically mentions that Expression 2 is the right hand 
side.',
        'is_correct': False,
        'orig_answer': (
            5,
            'Expression 1 = Expression 2\nthe term Expression 2 is the right hand side.',
            '<s> [INST] Your task is to disambiguate mathematical definitions.\nReply with "I don\'t know" when 
uncertain. \nOnly answer with the number corresponding to the correct choice in the provided list. \nDo not provide
justifications.\nIdentify the correct definition title from this list: \n1. Right (Direction)\n2. Right Angle\n3. 
Right Hand Side\n4. Right-Total Relation\n5. Right Quasi-Reflexive Relation\n6. Euclidean 
Relation/Right-Euclidean\n7. Right Normal Element of Relation\n8. Right Cancellable Mapping\n9. Right Inverse 
Mapping\n10. Interval/Ordered Set/Right Half-Open\n11. Orientation of Coordinate Axes/Cartesian 
Plane/Right-Handed\n12. Orientation of Coordinate Axes/Cartesian 3-Space/Right-Handed\n13. Limit of Real 
Function/Right\n14. Difference Quotient/Right\n15. Continuous Real Function/Right-Continuous\n16. Right-Hand 
Derivative/Real Function\n17. Real Interval/Half-Open/Right\n18. Real Interval/Unbounded Closed\n19. Real 
Interval/Unbounded Open\n20. Right Zero\n21. Identity (Abstract Algebra)/Right Identity\n22. Right Operation\n23. 
Cancellable Element/Right Cancellable\n24. Right Cancellable Operation\n25. Distributive Operation/Right\n26. 
Inverse (Abstract Algebra)/Right Inverse\n27. Quasigroup/Right Quasigroup\n28. Regular Representations/Right 
Regular Representation\n29. Operation/Binary Operation/Product/Right\n30. Right Naturally Totally Ordered 
Semigroup\n31. Coset/Right Coset\n32. Coset Space/Right Coset Space\n33. Transversal (Group Theory)/Right 
Transversal\n34. Group Action/Right Group Action\n35. Subset Product Action/Right\n36. Congruence Modulo 
Subgroup/Right Congruence\n37. Right Zero Divisor\n38. Linear Ring Action/Right\n39. Ideal of Ring/Right Ideal\n40.
Maximal Ideal of Ring/Right\n41. Right Module\n42. Right-Truncatable Prime\n43. Category of Right Modules\nGiven 
the term Rightand the following definition as context: \nIn an equation:\n:Expression 1 = Expression 2\nthe term 
Expression 2 is the right hand side. [/INST] 13. Limit of Real Function/Right\n14. Difference Quotient/Right\n15. 
Continuous Real Function/Right-Continuous\n16. Real Interval/Half-Open/Right\n17. Real Interval/Unbounded 
Closed\n18. Real Interval/Unbounded Open\n19. Right Zero\n20. Identity (Abstract Algebra)/Right Identity\n21. Right
Operation\n22. Cancellable Element/Right Cancellable\n23. Right Cancellable Operation\n24. Distributive 
Operation/Right\n25. Inverse (Abstract Algebra)/Right Inverse\n26. Quasigroup/Right Quasigroup\n27. Regular 


# Cleanup

In [29]:
import torch, gc
model = None
tokenizer = None
encodeds = None

gc.collect()

del encodeds
del tokenizer
del model

torch.cuda.empty_cache()